In [2]:
# Imports
import numpy as np
import pandas as pd
import altair as alt
from sklearn.model_selection import train_test_split
import statsmodels.api as sm
from statsmodels.stats.outliers_influence import variance_inflation_factor
# Allow Altair to make plots using more than 5000 rows
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

### Step 1: Describe the Dataset

This dataset first emerged in 1997 in a paper titled Sparse Spatial Autoregressions. It was collected by Pace, R. Kelley and Ronald Barry.
Each row in the dataset contains details for a single block group in California.
The data collected contains information about the houses for each block group and also details about the population in the city. The data was collected in 1990.

### Step 2: Load the Dataset

In [4]:
data = pd.read_csv('https://github.com/ageron/handson-ml/blob/master/datasets/housing/housing.csv?raw=true')

data.head()

longitude  latitude  housing_median_age  total_rooms  total_bedrooms  \
0    -122.23     37.88                41.0        880.0           129.0   
1    -122.22     37.86                21.0       7099.0          1106.0   
2    -122.24     37.85                52.0       1467.0           190.0   
3    -122.25     37.85                52.0       1274.0           235.0   
4    -122.25     37.85                52.0       1627.0           280.0   

   population  households  median_income  median_house_value ocean_proximity  
0       322.0       126.0         8.3252            452600.0        NEAR BAY  
1      2401.0      1138.0         8.3014            358500.0        NEAR BAY  
2       496.0       177.0         7.2574            352100.0        NEAR BAY  
3       558.0       219.0         5.6431            341300.0        NEAR BAY  
4       565.0       259.0         3.8462            342200.0        NEAR BAY

In [5]:
data.shape

(20640, 10)

### Step 5: Wrangling (do this earlier to split on train and test data before EDA)

In [6]:
# drop rows with NA values
data = data.dropna()

# drop longitude and latitude columns
data = pd.DataFrame.drop(data, columns=['longitude', 'latitude'])

# change median_income to tens of thousands of dollars
data['median_income'] = data['median_income']*10000

# move median_house_value to last column for formatting
columns = ['housing_median_age', 'total_rooms', 'total_bedrooms', 'population',
           'households', 'median_income', 'ocean_proximity']
X = data[columns]
y = data['median_house_value']

# Sources:
# https://stackoverflow.com/questions/13148429/how-to-change-the-order-of-dataframe-columns

In [15]:
# Split the dataset into train and test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3)

### Step 3: Explore the Dataset

In [16]:
X_train.describe(include='all')

housing_median_age   total_rooms  total_bedrooms    population  \
count         14303.000000  14303.000000    14303.000000  14303.000000   
unique                 NaN           NaN             NaN           NaN   
top                    NaN           NaN             NaN           NaN   
freq                   NaN           NaN             NaN           NaN   
mean             28.627421   2636.957212      537.716423   1423.261903   
std              12.629676   2184.326708      422.363917   1146.714302   
min               1.000000      2.000000        1.000000      3.000000   
25%              18.000000   1448.500000      295.000000    787.500000   
50%              29.000000   2130.000000      434.000000   1164.000000   
75%              37.000000   3157.000000      647.000000   1722.000000   
max              52.000000  39320.000000     6445.000000  35682.000000   

          households  median_income ocean_proximity  
count   14303.000000   14303.000000           14303  
unique           NaN            NaN               5  
top              NaN            NaN       <1H OCEAN  
freq             NaN            NaN            6322  
mean      499.274278   38740.816122             NaN  
std       383.845043   18966.381666             NaN  
min         1.000000    4999.000000             NaN  
25%       279.000000   25653.500000             NaN  
50%       409.000000   35380.000000             NaN  
75%       605.000000   47424.000000             NaN  
max      6082.000000  150001.000000             NaN

In [17]:
print("There are {0} records in the training portion of the dataset. Each record is a census block group.\n".format(
    X_train.count().min()))

print("The median age of houses/complexes in census blocks ranges from {0} to {1} with a mean of {2} years old and a median of {3} years old.\n".format(
    X_train['housing_median_age'].min(),
    X_train['housing_median_age'].max(),
    round(X_train['housing_median_age'].mean(), 2),
    X_train['housing_median_age'].median()))

print("The total number of rooms in a census block ranges from {0} to {1} with a mean of {2} rooms and a median of {3} rooms.\n".format(
    X_train['total_rooms'].min(),
    X_train['total_rooms'].max(),
    round(X_train['total_rooms'].mean(), 2),
    X_train['total_rooms'].median()))

print("The number of bedrooms in a census block ranges from {0} to {1} with a mean of {2} bedrooms and a median of {3} bedrooms.\n".format(
    X_train['total_bedrooms'].min(),
    X_train['total_bedrooms'].max(),
    round(X_train['total_bedrooms'].mean(), 2),
    X_train['total_bedrooms'].median()))

print("The population of a census block ranges from {0} to {1} with a mean of {2} and a median of {3}.\n".format(
    X_train['population'].min(),
    X_train['population'].max(),
    round(X_train['population'].mean(), 2),
    X_train['population'].median()))

print("The number of households in a census block ranges from {0} to {1} with a mean of {2} and a median of {3}.\n".format(
    X_train['households'].min(),
    X_train['households'].max(),
    round(X_train['households'].mean(), 2),
    data['households'].median()))

print("The median annual income in a census block ranges from ${0} to ${1} with a mean of ${2} and a median of ${3}.\n".format(
    X_train['median_income'].min(),
    X_train['median_income'].max(),
    round(X_train['median_income'].mean(), 2),
    X_train['median_income'].median()))

print("Ocean Proximity is a categorical value with one of the values:\n\t{0}, \n\t{1} (very close to the ocean), \n\t{2}, \n\t{3}, \n\t{4}.\n".format(
    X_train['ocean_proximity'].unique()[0].lower(),
    X_train['ocean_proximity'].unique()[1].lower(),
    X_train['ocean_proximity'].unique()[2].lower(),
    X_train['ocean_proximity'].unique()[3].lower(),
    X_train['ocean_proximity'].unique()[4].lower()))

print("The median house value in a census block ranges from ${0} to ${1} with a mean of ${2} and a median of ${3}.\n".format(
    y_train.min(),
    y_train.max(),
    round(y_train.mean(), 2),
    y_train.median()))

There are 14303 records in the training portion of the dataset. Each record is a census block group.

The median age of houses/complexes in census blocks ranges from 1.0 to 52.0 with a mean of 28.63 years old and a median of 29.0 years old.

The total number of rooms in a census block ranges from 2.0 to 39320.0 with a mean of 2636.96 rooms and a median of 2130.0 rooms.

The number of bedrooms in a census block ranges from 1.0 to 6445.0 with a mean of 537.72 bedrooms and a median of 434.0 bedrooms.

The population of a census block ranges from 3.0 to 35682.0 with a mean of 1423.26 and a median of 1164.0.

The number of households in a census block ranges from 1.0 to 6082.0 with a mean of 499.27 and a median of 409.0.

The median annual income in a census block ranges from $4999.0 to $150001.0 with a mean of $38740.82 and a median of $35380.0.

Ocean Proximity is a categorical value with one of the values:
	<1h ocean, 
	inland (very close to the ocean), 
	near ocean, 
	near bay, 
	island

In [18]:
data.sort_values(by = 'median_income').head(10)

housing_median_age  total_rooms  total_bedrooms  population  \
7125                 36.0         15.0             5.0        15.0   
4861                 29.0        515.0           229.0      2690.0   
73                   46.0         12.0             4.0        18.0   
20091                43.0        102.0            19.0        44.0   
13999                10.0        337.0           102.0       108.0   
6343                 52.0         62.0             9.0        44.0   
6688                 28.0        238.0            58.0       142.0   
5213                 52.0        117.0            33.0        74.0   
19523                52.0        178.0            53.0       152.0   
19800                15.0        661.0           146.0       131.0   

       households  median_income  median_house_value ocean_proximity  
7125          6.0         4999.0            162500.0       <1H OCEAN  
4861        217.0         4999.0            500001.0       <1H OCEAN  
73            7.0         4999.0             67500.0        NEAR BAY  
20091        13.0         4999.0            162500.0          INLAND  
13999        50.0         4999.0             55000.0          INLAND  
6343         16.0         4999.0            112500.0          INLAND  
6688         31.0         4999.0            500001.0          INLAND  
5213         45.0         4999.0             90600.0       <1H OCEAN  
19523        62.0         4999.0             82500.0          INLAND  
19800        57.0         4999.0             56700.0          INLAND

In [19]:
data.sort_values(by = 'housing_median_age').head(10)

housing_median_age  total_rooms  total_bedrooms  population  \
3130                  1.0         83.0            15.0        32.0   
19536                 1.0       2254.0           328.0       402.0   
12286                 1.0          6.0             2.0         8.0   
18972                 1.0       2062.0           343.0       872.0   
2339                  2.0       2579.0           376.0      1133.0   
16566                 2.0       2239.0           321.0       766.0   
10529                 2.0       2530.0           562.0      1066.0   
12006                 2.0      17978.0          3217.0      7305.0   
17824                 2.0       1136.0           365.0       535.0   
12142                 2.0       1424.0           251.0       681.0   

       households  median_income  median_house_value ocean_proximity  
3130         15.0        48750.0            141700.0          INLAND  
19536       112.0        42500.0            189200.0          INLAND  
12286         2.0        16250.0             55000.0          INLAND  
18972       268.0        52636.0            191300.0          INLAND  
2339        342.0        45577.0            123300.0          INLAND  
16566       219.0        57500.0            240200.0          INLAND  
10529       510.0        46336.0            187500.0       <1H OCEAN  
12006      2463.0        51695.0            220800.0          INLAND  
17824       257.0        43750.0            425000.0       <1H OCEAN  
12142       192.0        40833.0            100000.0          INLAND

In [20]:
data.sort_values(by = 'median_house_value').head(10)

housing_median_age  total_rooms  total_bedrooms  population  \
9188                 52.0        803.0           267.0       628.0   
2521                 16.0        255.0            73.0        85.0   
2799                 19.0        619.0           239.0       490.0   
19802                36.0         98.0            28.0        18.0   
5887                 39.0        493.0           168.0       259.0   
13889                 8.0       9975.0          1743.0      6835.0   
1825                 33.0        296.0            73.0       216.0   
16186                52.0        107.0            79.0       167.0   
14326                52.0        845.0           451.0      1230.0   
2779                 21.0         44.0            33.0        64.0   

       households  median_income  median_house_value ocean_proximity  
9188        225.0        41932.0             14999.0          INLAND  
2521         38.0        16607.0             14999.0          INLAND  
2799        164.0        21000.0             14999.0          INLAND  
19802         8.0         5360.0             14999.0          INLAND  
5887        138.0        23667.0             17500.0       <1H OCEAN  
13889      1439.0        27138.0             22500.0          INLAND  
1825         63.0        26750.0             22500.0        NEAR BAY  
16186        53.0         7917.0             22500.0          INLAND  
14326       375.0        10918.0             22500.0      NEAR OCEAN  
2779         27.0         8571.0             25000.0          INLAND

### Step 4: Initial Thoughts about the Dataset

* Blocks vary drastically in the number of bedrooms and total number of rooms. 
* Lowest median income blocks differ in the number of housholds (some highly populated blocks have very low income).
* New houses vary in their value (interseting to study the relationship between age and value).
* 7 out of the 10 Lowest-value houses are INLAND. (is being near the ocean affect has a direct relationship with its value)

### Step 6: Research Questions

* Can we predict the mean household value for a block given some data?

### Step 7: Data Analysis and Visualizations

In [21]:
# For visualizations, combine X_train and y_train
viz_data = pd.merge(X_train, y_train, left_index=True, right_index=True)

In [22]:
def make_chart(x, x_title):
    """
    Creates an altair scatterplot with the input on the x-axis and 
    the median house value on the y-axis
    
    Parameters
    ----------
    x: string
        the column name of the x-axis column to be created
    x_title: string
        the title of the x-axis (and to be used in the chart title)
    
    Returns
    ----------
    altair chart object
        scatterplot of defined x compared to median house value
    """
    chart = alt.Chart(viz_data).mark_point(opacity=0.2).encode(
        alt.X(x, title=x_title),
        alt.Y('median_house_value:Q', title="Median House Value")
    ).properties(
        width=200,
        height=200,
        title="Median House Value per " + x_title
    )
    
    return chart

row1 = make_chart('housing_median_age', "House Median Age") | make_chart('total_rooms', "Total Rooms")
row2 = make_chart('total_bedrooms', "Total Bedrooms") | make_chart('population', "Population")
row3 = make_chart('households', "Households") | make_chart('median_income', "Median Income")
row1 & row2 & row3

# Sources:
# https://stackoverflow.com/questions/51540027/how-to-make-an-altair-plot-within-an-if-statement

alt.VConcatChart(...)

In [23]:
# Look at the relationship between total_rooms and total_bedrooms
alt.Chart(viz_data).mark_point(opacity=0.2).encode(
    alt.X('total_bedrooms', title="Total Bedrooms"),
    alt.Y('total_rooms', title="Total Rooms")
).properties(
    width=350,
    height=300,
    title="Relationship between Bedroom and Room Counts"
)

alt.Chart(...)

In [24]:
# Find Variance Inflation Factor

# drop ocean_proximity column for this
mc_data = pd.DataFrame.drop(X_train, columns='ocean_proximity')
mc_data['intercept'] = 1

In [25]:
# Initialize a dataframe to store Variance Inflation Factors in
mc_data.shape[1]
vif = pd.DataFrame()
vif['variable'] = mc_data.columns
vif['vif_val'] = [variance_inflation_factor(mc_data.values, i) for i in range(mc_data.shape[1])]
vif

# Sources:
# https://campus.datacamp.com/courses/generalized-linear-models-in-python/multivariable-logistic-regression?ex=4

variable    vif_val
0  housing_median_age   1.164987
1         total_rooms  11.643747
2      total_bedrooms  36.784298
3          population   6.050949
4          households  35.286351
5       median_income   1.496982
6           intercept  17.784874

In [26]:
# Violin Plot for ocean_proximity
# 
alt.Chart(viz_data).mark_area(orient='horizontal').transform_density(
    'median_house_value',
    as_=['median_house_value', 'density'],
    groupby=['ocean_proximity']
).encode(
    y= alt.Y('median_house_value:Q', title = None),
    color=alt.Color('ocean_proximity:N', title = None),
    x=alt.X(
        'density:Q',
        stack='center',
        impute=None,
        title=None,
        axis=alt.Axis(labels=False, values=[0],grid=False, ticks=True),
    ),
    column=alt.Column(
        'ocean_proximity:N',
        header=alt.Header(
            titleOrient='bottom',
            labelOrient='bottom',
            labelPadding=0,
            title = None
        ),
    )
).properties(
    width=150,
    height = 300
)

alt.Chart(...)

In [27]:
# Finding the correlation matrix
corrMatrix = viz_data.corr()
corrMatrix['names'] = corrMatrix.columns
corrMatrix = corrMatrix.melt(id_vars = 'names', value_vars = corrMatrix['names'])

In [28]:

alt.Chart(corrMatrix).mark_rect().encode(
    x = alt.X('names:O', title = None),
    y = alt.Y('variable:O', title = None),
    color= alt.Color('value:Q', title = 'Correlation Value')
).properties(width = 400, height = 300, title = "Correlation Heatmap")

alt.Chart(...)

### Step 8: Summary and Conclusions

* There is a high correlation between the number of househoolds, bedrooms, rooms and the population.

* The location in respect to the ocean affects the household values.

* Households near the ocean and households near the bay have similar value ranges.

* Data is not linear and a transformation of the data is needed to perform regressions. 

* As the households values have a high variance, different models need to be evaluated and compared.